In [41]:
import pandas as pd
import numpy as np
import re
import nltk.corpus
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import Counter
from sklearn.cross_validation import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from sklearn.linear_model import LogisticRegression

%matplotlib inline

In [4]:
with open('yelp_academic_dataset_review.json', 'rb') as f:
    data = f.readlines()

data = map(lambda x: x.rstrip(), data)
data_json_str = "[" + ','.join(data) + "]"

review_df = pd.read_json(data_json_str)

In [5]:
voteslst=[]
for i in review_df['votes']:
    voteslst.append(i)

In [6]:
votes=pd.DataFrame(voteslst)

In [7]:
votes['useful'].max()

167

In [8]:
votes[votes['cool']==138]

cool  funny  useful
1512459   138    142     167

In [9]:
best_review=review_df['text'][1512459]
best_review

u'I\'m the first real person to review this place, let all other fake spammers be gone!  Yelp should really work that shizzle out.  Zack S...um this place closes at 11 so you couldn\'t have possibly hit the bar...so yeah if your gonna post fake reviews at least check your facts..\n\nThis place has so much potential, yet the ridiculously bad service just overshadowed everything good they did.\n\nThis is probably the worst service I have ever received in my life.  \n\nDo you guys remember in Pretty Woman when Julia Roberts goes into the first store on Rodeo and the snooty lady acts like she\'s too good for this place?  Well that\'s what they did to us.\n\nWhere\'s the hostess?  Oh she\'s chatting with her friend...*ignoring me*\n\nWe finally get seated and then we sit and wait...\n\nand wait...\n\nand wait...\n\nfinally I get up and ask one of the waiters at the cash register to send over someone...\n\nShe treats us like we\'re a nuisance to her, she\'s singing along to the song that\'s 

In [10]:
regex_str = [r'(?:(?:\d+,?)+(?:\.?\d+)?)', # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])", # words with - and '
    r'(?:[\w_]+)', # other words
    r'(?:\S)' # anything else
             ]
tokens_re = re.compile(r'('+'|'.join(regex_str)+')', re.VERBOSE | re.IGNORECASE)

def tokenize(s):
    return tokens_re.findall(s)

def preprocess(s, lowercase=False):
    tokens = tokenize(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

In [12]:
print(preprocess(best_review))

[u"I'm", u'the', u'first', u'real', u'person', u'to', u'review', u'this', u'place', u',', u'let', u'all', u'other', u'fake', u'spammers', u'be', u'gone', u'!', u'Yelp', u'should', u'really', u'work', u'that', u'shizzle', u'out', u'.', u'Zack', u'S', u'.', u'.', u'.', u'um', u'this', u'place', u'closes', u'at', u'11', u'so', u'you', u"couldn't", u'have', u'possibly', u'hit', u'the', u'bar', u'.', u'.', u'.', u'so', u'yeah', u'if', u'your', u'gonna', u'post', u'fake', u'reviews', u'at', u'least', u'check', u'your', u'facts', u'.', u'.', u'This', u'place', u'has', u'so', u'much', u'potential', u',', u'yet', u'the', u'ridiculously', u'bad', u'service', u'just', u'overshadowed', u'everything', u'good', u'they', u'did', u'.', u'This', u'is', u'probably', u'the', u'worst', u'service', u'I', u'have', u'ever', u'received', u'in', u'my', u'life', u'.', u'Do', u'you', u'guys', u'remember', u'in', u'Pretty', u'Woman', u'when', u'Julia', u'Roberts', u'goes', u'into', u'the', u'first', u'store', u'o

In [24]:
from nltk.corpus import stopwords

In [26]:
stopwords.words('english')

[u'i',
 u'me',
 u'my',
 u'myself',
 u'we',
 u'our',
 u'ours',
 u'ourselves',
 u'you',
 u'your',
 u'yours',
 u'yourself',
 u'yourselves',
 u'he',
 u'him',
 u'his',
 u'himself',
 u'she',
 u'her',
 u'hers',
 u'herself',
 u'it',
 u'its',
 u'itself',
 u'they',
 u'them',
 u'their',
 u'theirs',
 u'themselves',
 u'what',
 u'which',
 u'who',
 u'whom',
 u'this',
 u'that',
 u'these',
 u'those',
 u'am',
 u'is',
 u'are',
 u'was',
 u'were',
 u'be',
 u'been',
 u'being',
 u'have',
 u'has',
 u'had',
 u'having',
 u'do',
 u'does',
 u'did',
 u'doing',
 u'a',
 u'an',
 u'the',
 u'and',
 u'but',
 u'if',
 u'or',
 u'because',
 u'as',
 u'until',
 u'while',
 u'of',
 u'at',
 u'by',
 u'for',
 u'with',
 u'about',
 u'against',
 u'between',
 u'into',
 u'through',
 u'during',
 u'before',
 u'after',
 u'above',
 u'below',
 u'to',
 u'from',
 u'up',
 u'down',
 u'in',
 u'out',
 u'on',
 u'off',
 u'over',
 u'under',
 u'again',
 u'further',
 u'then',
 u'once',
 u'here',
 u'there',
 u'when',
 u'where',
 u'why',
 u'how',
 u'all

In [31]:
from nltk.corpus import stopwords
import string
 
punctuation = list(string.punctuation)
stop = stopwords.words('english') + punctuation

terms_stop = [term for term in preprocess(best_review) if term not in stop]

In [32]:
terms_stop

[u"I'm",
 u'first',
 u'real',
 u'person',
 u'review',
 u'place',
 u'let',
 u'fake',
 u'spammers',
 u'gone',
 u'Yelp',
 u'really',
 u'work',
 u'shizzle',
 u'Zack',
 u'S',
 u'um',
 u'place',
 u'closes',
 u'11',
 u"couldn't",
 u'possibly',
 u'hit',
 u'bar',
 u'yeah',
 u'gonna',
 u'post',
 u'fake',
 u'reviews',
 u'least',
 u'check',
 u'facts',
 u'This',
 u'place',
 u'much',
 u'potential',
 u'yet',
 u'ridiculously',
 u'bad',
 u'service',
 u'overshadowed',
 u'everything',
 u'good',
 u'This',
 u'probably',
 u'worst',
 u'service',
 u'I',
 u'ever',
 u'received',
 u'life',
 u'Do',
 u'guys',
 u'remember',
 u'Pretty',
 u'Woman',
 u'Julia',
 u'Roberts',
 u'goes',
 u'first',
 u'store',
 u'Rodeo',
 u'snooty',
 u'lady',
 u'acts',
 u'like',
 u"she's",
 u'good',
 u'place',
 u'Well',
 u"that's",
 u'us',
 u"Where's",
 u'hostess',
 u'Oh',
 u"she's",
 u'chatting',
 u'friend',
 u'ignoring',
 u'We',
 u'finally',
 u'get',
 u'seated',
 u'sit',
 u'wait',
 u'wait',
 u'wait',
 u'finally',
 u'I',
 u'get',
 u'ask',


In [14]:
Counter(preprocess(best_review)).most_common(10)

[(u'.', 71),
 (u'the', 22),
 (u'I', 17),
 (u'to', 15),
 (u'and', 14),
 (u',', 12),
 (u'a', 10),
 (u'have', 9),
 (u'?', 8),
 (u'!', 8)]

In [15]:
vectorizer = CountVectorizer(max_features = 1000,
                             ngram_range=(1, 2),
                             stop_words='english',
                             binary=True)
vectorizer.fit(preprocess(best_review))
len(vectorizer.get_feature_names())

176

In [16]:
tokens = pd.DataFrame(vectorizer.transform(preprocess(best_review)).todense(),
                       columns=vectorizer.get_feature_names())
tokens.head()

11  200  acts  anthony  apparently  asian  ask  attitude  avoid  away  \
0   0    0     0        0           0      0    0         0      0     0   
1   0    0     0        0           0      0    0         0      0     0   
2   0    0     0        0           0      0    0         0      0     0   
3   0    0     0        0           0      0    0         0      0     0   
4   0    0     0        0           0      0    0         0      0     0   

   ...   woman  won  work  worst  worth  wtf  yeah  yelp  yelped  zack  
0  ...       0    0     0      0      0    0     0     0       0     0  
1  ...       0    0     0      0      0    0     0     0       0     0  
2  ...       0    0     0      0      0    0     0     0       0     0  
3  ...       0    0     0      0      0    0     0     0       0     0  
4  ...       0    0     0      0      0    0     0     0       0     0  

[5 rows x 176 columns]

In [17]:
word_counts = tokens.sum(axis=0)
word_counts.sort_values(ascending = False).head(20)

place         7
like          7
restaurant    6
wait          5
waiters       3
seriously     3
service       3
don           3
ridiculous    3
nice          2
people        2
did           2
worst         2
really        2
chatting      2
left          2
good          2
time          2
experience    2
life          2
dtype: int64

In [18]:
most_reviews=review_df[review_df['business_id']=='4bEjOyTaDG24SY5TxsaUNQ']
most_reviews.head()

business_id       date               review_id  stars  \
510273  4bEjOyTaDG24SY5TxsaUNQ 2005-06-23  UpKdXO3jEElnqtsWjYxQ2w      5   
510274  4bEjOyTaDG24SY5TxsaUNQ 2005-10-10  qYJV5kIViwer1P1Cb2OSfw      5   
510275  4bEjOyTaDG24SY5TxsaUNQ 2005-10-14  dvSLFLzijuT5HLRlmt5FaA      5   
510276  4bEjOyTaDG24SY5TxsaUNQ 2005-12-02  y79Q4oMPl-7yFvAIhep18g      4   
510277  4bEjOyTaDG24SY5TxsaUNQ 2006-01-07  yZ-XOxrnx9QKGCgDxIFRag      4   

                                                     text    type  \
510273  Excellent food, great atmosphere, a bit noisy....  review   
510274  If you enjoy a little people watching with you...  review   
510275  affordable, fairly classic french food\n\nsit ...  review   
510276  Though heartbroken and a bit aimless on my 22n...  review   
510277  The food and wine was amazing, but the super h...  review   

                       user_id                                    votes  
510273  LAOHN2Z6INbwuGa3fx9UTw  {u'funny': 0, u'useful': 0, u'cool': 0}  
510274  H43f_rD3czq0UqY-4zhWjA  {u'funny': 0, u'useful': 0, u'cool': 0}  
510275  ytjqLRFobRxl0DDJgoR-Eg  {u'funny': 2, u'useful': 2, u'cool': 2}  
510276  pW91HUnVz6ssLZ4dY-ztyQ  {u'funny': 2, u'useful': 3, u'cool': 3}  
510277  aoxuw-XpJYIX1-R0TUS7CQ  {u'funny': 0, u'useful': 1, u'cool': 0}

In [19]:
for i in most_reviews['text']:
    tokens=(preprocess(i))
    print tokens

[u'Excellent', u'food', u',', u'great', u'atmosphere', u',', u'a', u'bit', u'noisy', u'.', u'$', u'$']
[u'If', u'you', u'enjoy', u'a', u'little', u'people', u'watching', u'with', u'your', u'dining', u',', u'sit', u'out', u'on', u'the', u'outside', u'terrace', u'and', u'watch', u'Las', u'Vegas', u'tourist', u'walk', u'the', u'strip', u'as', u'they', u'celebrate', u'their', u'winnings', u'or', u'rave', u'about', u'the', u'fabulous', u'Bellagio', u'fountains', u'.', u'As', u'the', u'restaurant', u'is', u'directly', u'across', u'from', u'the', u'fountains', u',', u'it', u'is', u'also', u'a', u'great', u'place', u'to', u'dine', u'while', u'taking', u'in', u'the', u'free', u'show', u'.', u'The', u'food', u'fits', u'the', u'setting', u',', u'with', u'a', u'traditional', u'French', u'menu', u'infused', u'with', u'a', u'bit', u'of', u'Vegas', u'penache', u'.', u'We', u'had', u'excellent', u'service', u'.', u'.', u'polite', u',', u'prompt', u',', u'helpful', u'(', u'great', u'at', u'helping', u'

In [20]:
Counter(tokens)

Counter({u'!': 2,
         u'"': 2,
         u'-': 1,
         u'.': 3,
         u'Amazing': 1,
         u'Benedict': 1,
         u'Big': 1,
         u'Eggs': 1,
         u'Had': 1,
         u'Skinny': 1,
         u'The': 1,
         u'also': 1,
         u'delicious': 1,
         u'pancakes': 1,
         u'were': 1,
         u'wonderful': 1})

In [9]:
vectorizer = CountVectorizer(max_features = 1000,
                             ngram_range=(1, 2),
                             stop_words='english',
                             binary=True)
vectorizer.fit(preprocess(tokens))
len(vectorizer.get_feature_names())

TypeError: expected string or buffer

In [45]:
for i in most_reviews['text']:
    print i

Excellent food, great atmosphere, a bit noisy.  $$
If you enjoy a little people watching with your dining, sit out on the outside terrace and watch Las Vegas tourist walk the strip as they celebrate their winnings or rave about the fabulous Bellagio fountains.  As the restaurant is directly across from the fountains, it is also a great place to dine while taking in the free show.   The food fits the setting, with a traditional French menu infused with a bit of Vegas penache.   We had excellent service..polite, prompt, helpful (great at helping us pick a great wine suited to our selections!) and personal.   And by the way,   the wait staff aren't above snapping that great snapshot of you and your guest having a good time....it is great to be a tourist!
affordable, fairly classic french food

sit outside if you like to people watch

or 

see the bellagio fountain show

very reminiscent of paris
(on steroids!)
Though heartbroken and a bit aimless on my 22nd birthday, a meal at Mon Ami Gab

In [46]:
vectorizer = CountVectorizer(max_features = 1000,
                             ngram_range=(3, 3),
                             stop_words='english',
                             binary=True)
vectorizer.fit(most_reviews['text'])
len(vectorizer.get_feature_names())

1000

In [47]:
tokens = pd.DataFrame(vectorizer.transform(most_reviews['text']).todense(),
                       columns=vectorizer.get_feature_names())
tokens.head()

10 15 minutes  10 minute wait  20 minute wait  20 minutes table  \
0              0               0               0                 0   
1              0               0               0                 0   
2              0               0               0                 0   
3              0               0               0                 0   
4              0               0               0                 0   

   22 oz bone  30 minute wait  45 minute wait  able sit outside  \
0           0               0               0                 0   
1           0               0               0                 0   
2           0               0               0                 0   
3           0               0               0                 0   
4           0               0               0                 0   

   able watch bellagio  absolutely love place     ...       white wine sauce  \
0                    0                      0     ...                      0   
1                    0                      0     ...                      0   
2                    0                      0     ...                      0   
3                    0                      0     ...                      0   
4                    0                      0     ...                      0   

   wild escargots bourgogne  wine reduction sauce  wonderful view bellagio  \
0                         0                     0                        0   
1                         0                     0                        0   
2                         0                     0                        0   
3                         0                     0                        0   
4                         0                     0                        0   

   wrapped pork tenderloin  wrong mon ami  www yelp com  yelp com biz_photos  \
0                        0              0             0                    0   
1                        0              0             0                    0   
2                        0              0             0                    0   
3                        0              0             0                    0   
4                        0              0             0                    0   

   york strip steak  yum yum yum  
0                 0            0  
1                 0            0  
2                 0            0  
3                 0            0  
4                 0            0  

[5 rows x 1000 columns]

In [49]:
word_counts = tokens.sum(axis=0)

word_counts.sort_values(ascending = False).head(45)

mon ami gabi                883
french onion soup           412
view bellagio fountains     292
filet mignon merlot         111
bloody mary bar             108
view bellagio fountain      107
great view bellagio         105
view bellagio water          76
food great service           73
corned beef hash             72
seated right away            66
steak au poivre              64
baked goat cheese            63
mignon merlot butter         59
las vegas strip              58
great food great             57
great people watching        53
service great food           51
great service great          49
chicken brie sandwich        49
gluten free menu             48
blueberry french toast       46
red wine sauce               45
red wine reduction           45
watch bellagio fountains     43
ordered steak frites         42
chicken liver mousse         40
ordered filet mignon         39
located paris hotel          38
ami gabi great               37
beautiful view bellagio      35
sit outs

In [42]:
train, test = train_test_split(most_reviews['text'], train_size = 0.8)

models = [KNeighborsClassifier(),
          LogisticRegression(),
          DecisionTreeClassifier(),
          SVC(),
          RandomForestClassifier(),
          ExtraTreesClassifier()]

tvec = TfidfVectorizer(stop_words='english',
                       sublinear_tf=True,
                       max_df=0.5,
                       max_features=1000)



In [43]:
tvec.fit(train)
train = tvec.transform(train)
test = tvec.transform(test)

In [44]:
res = []

for model in models:
    print model
    model.fit(train, train)
    y_pred = model.predict(test)
    score = accuracy_score(test, pred)
    print score
    cm = docm(test, pred, names)
    print cm
    res.append([model, score])


KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=5, p=2,
           weights='uniform')


TypeError: len() of unsized object

In [41]:
from textblob.classifiers import NaiveBayesClassifier

train=[('great service' ,'pos'),
      ('good food', 'pos'),
       ('Excellent food, great atmosphere', 'pos'),
       ('The open kitchen has been known to cause mouth watering experiences due  to the glorious aromas in an already pleasant environment', 'pos'),
       ('We had excellent service..polite, prompt, helpful (great at helping us pick a great wine suited to our selections!) and personal.', 'pos')
     , ('Don\'t waste your time.', 'neg'),
       ('The food is mediocre at best but their attitude sucks', 'neg'),
       ('The food was dry and tasteless', 'neg'),
       ('long wait time and bad service', 'neg'),
       ('Third Section going towards the rear of the cafe is not an ideal area to be seated.','neg')
]

cl = NaiveBayesClassifier(train)

In [42]:
prob_dist = cl.prob_classify("The waiter was great and definitely made the experience better.")
round(prob_dist.prob("pos"), 2)

0.28

In [43]:
prob_dist = cl.prob_classify("Some of the waiters are not very friendly or personable.")
round(prob_dist.prob("pos"), 2)

0.03